In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.stats import norm
from collections import Counter
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC
import sklearn.metrics as metrics
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
from sklearn import preprocessing
from math import sqrt
from sklearn.model_selection import train_test_split
import time
import re
from tqdm import tqdm

In [2]:
#學生借什麼書
borrowing_record = pd.read_csv("borrowing_record.csv")
borrowing_record.sort_values(['借書時間','學生'],inplace=True)
borrowing_record.drop_duplicates(subset=['借書時間','學生'],inplace=True)
borrowing_record.reset_index(drop=True,inplace=True)
borrowing_record.head()

學生                 借書時間  \
0  e87b9e77cd438139f2735822b557d64e769898e0  2011/08/12 09:40:55   
1  e87b9e77cd438139f2735822b557d64e769898e0  2011/08/19 13:46:40   
2  e87b9e77cd438139f2735822b557d64e769898e0  2011/08/19 13:47:05   
3  e87b9e77cd438139f2735822b557d64e769898e0  2011/08/19 13:48:24   
4  88d9800e0720ce149af15703c01f63994dbbce26  2011/08/30 11:44:14   

                  還書時間        登錄號                  館藏索書號  \
0  2011/11/14 16:18:15  C00189827    178.2 4244 2004 c.2   
1  2011/11/14 16:18:08  C00126828     541.3208 4664 1991   
2  2011/11/14 16:18:06  C00001324       541.32 4664 1988   
3  2011/11/14 16:18:04  C00125606       541.32 5034 2000   
4  2011/10/20 14:12:47  C00269836  178.8 4415-2 2004 c.3   

                                           書名/作者:出版項  
0  挫折復原力/布魯克斯/戈爾茲坦/洪慧芳/Brooks Robert/Goldstein Sa...  
1                     中國人的心理與行為/楊國樞/黃光國/黃光國:,桂冠,1991  
2                                中國人的心理/楊國樞:,桂冠,1988  
3  中國人的性格/史密斯/樂愛國/張華玉/Smith Arthur H./樂愛國/張華玉:,三聯...  
4  悲傷輔導與悲傷治療:心理衛生實務工作者手冊/華爾頓/李開敏/Worden J. Willia...

In [3]:
#學生修什麼課程(drop_duplicates next part)
course_train = pd.read_csv("course_train.csv")
course_train.sort_values(['學年','學期','學生'],inplace=True)
course_train.reset_index(drop=True,inplace=True)
course_train.head()

學生      系所   學年  學期  年級 班級  \
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  資訊傳播學系  100   1   1  A   
1  0003764c18b55548b8e7e0a064fed87fb46fa2a2  資訊傳播學系  100   1   1  A   
2  0003764c18b55548b8e7e0a064fed87fb46fa2a2  資訊傳播學系  100   1   1  A   
3  0003764c18b55548b8e7e0a064fed87fb46fa2a2  資訊傳播學系  100   1   1  A   
4  0008612986afce01d430baec13e6ab111ff864a9  資訊傳播學系  100   1   1  B   

        開課系所 開課班級  開課年級      課程代碼     課程名稱  修別   學分  
0  (資)資傳系碩士班    A     1  75M00002     論文研討  必修  1.0  
1  (資)資傳系碩士班    A     1  75M00003   互動媒體設計  選修  3.0  
2  (資)資傳系碩士班    A     1  75M00004  專題研討(一)  必修  1.0  
3  (資)資傳系碩士班    A     1  75M00008   數位音訊處理  選修  3.0  
4     (資)資傳系    A     1  63U00033    軍訓(一)  必修  0.0

In [4]:
#圖書館進出時間(drop_duplicates under)
library_in_and_out_record = pd.read_csv("library_in_and_out_record.csv")
library_in_and_out_record.sort_values(['刷卡時間','學生'],inplace=True)
library_in_and_out_record.reset_index(drop=True,inplace=True)
library_in_and_out_record.head()

學生                 刷卡時間 管制項目
0  2e118d2d595f9ce636e52c22fd989f6240983ec8  2011-12-16 17:29:02    進
1  d138d66c345b4a5aa5ac96f29f90acefa1b41d0f  2011-12-17 09:50:58    進
2  d4fa91d126812f0ca13d411398268978d6d87d0f  2011-12-17 10:44:14    進
3  d138d66c345b4a5aa5ac96f29f90acefa1b41d0f  2011-12-17 14:13:09    進
4  0f35992a347531e4a721ee4cbd6b181fd0e111f8  2011-12-17 14:13:12    進

In [5]:
#查看進出圖書館資料筆數
print("進入次數:",len(library_in_and_out_record[library_in_and_out_record['管制項目']=='進']))
print("出去次數:",len(library_in_and_out_record[library_in_and_out_record['管制項目']=='出']))

進入次數: 717629
出去次數: 209660


In [6]:
#以進入次數作為圖書館時間
library_in_and_out_record=library_in_and_out_record[library_in_and_out_record['管制項目']=='進']
library_in_and_out_record.drop_duplicates(subset=['學生','刷卡時間'],inplace=True)
library_in_and_out_record.reset_index(drop=True,inplace=True)

In [7]:
#刪除重複學生排名資料
rank_train = pd.read_csv("rank_train.csv")
rank_train.sort_values(['學年','學期','學生'],inplace=True)
rank_train.drop_duplicates(subset=['學年','學期','學生'],inplace=True)
rank_train.reset_index(drop=True,inplace=True)
rank_train.head()

學生   學年  年級  學期  概化排名  排名差
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  100   1   1     5    0
1  0008612986afce01d430baec13e6ab111ff864a9  100   1   1   105    0
2  002aad264dbe66aeaf7ddfbd5afffd22e3930588  100   1   1    45    0
3  0037f157b190f25f6e06030ea2c5f9f62b429ea1  100   1   1    55    0
4  003a5db190ba04e18cbedba93306e7ebee670d96  100   1   1     5    0

# 書籍資料

In [8]:
chinese = pd.read_excel("中文圖書分類法.xls")
chinese.head()

分類號 分類項目名稱  勾選
0    0     特藏 NaN
1    1     善本 NaN
2    2     稿本 NaN
3    3    精鈔本 NaN
4    4    紀念藏 NaN

In [9]:
western = pd.read_excel("西文圖書美國國會分類法.xls")
western.head()

Unnamed: 0       美國國會分類法(LCC) Unnamed: 2  \
0           1  A ─ GENERAL WORKS          A   
1           2  A ─ GENERAL WORKS         AC   
2           3  A ─ GENERAL WORKS         AE   
3           4  A ─ GENERAL WORKS         AG   
4           5  A ─ GENERAL WORKS         AI   

                                       Unnamed: 3  勾選  
0                                   General Works NaN  
1            Collections. Series. Collected works NaN  
2                                   Encyclopedias NaN  
3  Dictionaries and other general reference works NaN  
4                                         Indexes NaN

In [10]:
america = pd.read_excel("美國國家醫學圖書館分類法.xlsx",header=1)
america.head()

Unnamed: 0 分類號                                    內容  Unnamed: 3
0           1  QS                   Human Anatomy 人體解剖學         NaN
1           2  QT                        Physiology 生理學         NaN
2           3  QU                     Biochemistry 生物化學         NaN
3           4  QV                      Pharmacology 藥理學         NaN
4           5  QW  Microbiology and Immunology 微生物學及免疫學         NaN

# 分割每一學期

In [11]:
#100學期上:2011/08/23~2012/01/13
#100學期下:2012/02/20~2012/06/22
#101學期上:2012/09/10~2013/01/11
#101學期下:2013/02/21~2013/06/26
#102學期上:2013/09/11~2014/01/14
#102學期下:2014/02/17~2014/06/20
#103學期上:2014/09/24~2015/01/27
#103學期下:2015/02/25~2015/06/30
#104學期上:2015/09/14~2016/01/15
#104學期下:2016/02/17~2016/06/21
#105學期上:2016/09/12~2017/01/13
#105學期下:2017/02/20~2017/06/23
#106學期上:2017/09/18~2018/01/19
#106學期下:2018/02/26~2018/06/29
#107學期上:2018/09/10~2019/01/11
#107學期下:2019/02/18~2019/06/21

In [12]:
#學生借什麼書
#borrowing_record_100_up
borrowing_record_100_up=borrowing_record[borrowing_record['借書時間']<'2012/01/13']
borrowing_record_100_down=borrowing_record[(borrowing_record['借書時間']>='2012/01/13')&(borrowing_record['借書時間']<'2012/06/22')]
borrowing_record_101_up=borrowing_record[(borrowing_record['借書時間']>='2012/06/22')&(borrowing_record['借書時間']<'2013/01/11')]
borrowing_record_101_down=borrowing_record[(borrowing_record['借書時間']>='2013/01/11')&(borrowing_record['借書時間']<'2013/06/26')]
borrowing_record_102_up=borrowing_record[(borrowing_record['借書時間']>='2013/06/26')&(borrowing_record['借書時間']<'2014/01/14')]
borrowing_record_102_down=borrowing_record[(borrowing_record['借書時間']>='2014/01/14')&(borrowing_record['借書時間']<'2014/06/20')]
borrowing_record_103_up=borrowing_record[(borrowing_record['借書時間']>='2014/06/20')&(borrowing_record['借書時間']<'2015/01/27')]
borrowing_record_103_down=borrowing_record[(borrowing_record['借書時間']>='2015/01/27')&(borrowing_record['借書時間']<'2015/06/30')]
borrowing_record_104_up=borrowing_record[(borrowing_record['借書時間']>='2015/06/30')&(borrowing_record['借書時間']<'2016/01/15')]
borrowing_record_104_down=borrowing_record[(borrowing_record['借書時間']>='2016/01/15')&(borrowing_record['借書時間']<'2016/06/21')]
borrowing_record_105_up=borrowing_record[(borrowing_record['借書時間']>='2016/06/21')&(borrowing_record['借書時間']<'2017/01/13')]
borrowing_record_105_down=borrowing_record[(borrowing_record['借書時間']>='2017/01/13')&(borrowing_record['借書時間']<'2017/06/23')]
borrowing_record_106_up=borrowing_record[(borrowing_record['借書時間']>='2017/06/23')&(borrowing_record['借書時間']<'2018/01/19')]
borrowing_record_106_down=borrowing_record[(borrowing_record['借書時間']>='2018/01/19')&(borrowing_record['借書時間']<'2018/06/29')]
borrowing_record_107_up=borrowing_record[(borrowing_record['借書時間']>='2018/06/29')&(borrowing_record['借書時間']<'2019/01/11')]
#borrowing_record_107_down=borrowing_record[(borrowing_record['借書時間']>='2019/01/11')&(borrowing_record['借書時間']<'2019/06/21')]

In [13]:
#學生修什麼課程
#course_train_100_up
course_train_100_up=course_train[(course_train['學年']==100)&(course_train['學期']==1)]
course_train_100_down=course_train[(course_train['學年']==100)&(course_train['學期']==2)]
course_train_101_up=course_train[(course_train['學年']==101)&(course_train['學期']==1)]
course_train_101_down=course_train[(course_train['學年']==101)&(course_train['學期']==2)]
course_train_102_up=course_train[(course_train['學年']==102)&(course_train['學期']==1)]
course_train_102_down=course_train[(course_train['學年']==102)&(course_train['學期']==2)]
course_train_103_up=course_train[(course_train['學年']==103)&(course_train['學期']==1)]
course_train_103_down=course_train[(course_train['學年']==103)&(course_train['學期']==2)]
course_train_104_up=course_train[(course_train['學年']==104)&(course_train['學期']==1)]
course_train_104_down=course_train[(course_train['學年']==104)&(course_train['學期']==2)]
course_train_105_up=course_train[(course_train['學年']==105)&(course_train['學期']==1)]
course_train_105_down=course_train[(course_train['學年']==105)&(course_train['學期']==2)]
course_train_106_up=course_train[(course_train['學年']==106)&(course_train['學期']==1)]
course_train_106_down=course_train[(course_train['學年']==106)&(course_train['學期']==2)]
course_train_107_up=course_train[(course_train['學年']==107)&(course_train['學期']==1)]
#course_train_107_down=course_train[(course_train['學年']==107)&(course_train['學期']==2)]

In [14]:
#圖書館進出時間
#library_in_and_out_record_100_up
library_in_and_out_record_100_up=library_in_and_out_record[library_in_and_out_record['刷卡時間']<'2012/01/13']
library_in_and_out_record_100_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2012/01/13')&(library_in_and_out_record['刷卡時間']<'2012/06/22')]
library_in_and_out_record_101_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2012/06/22')&(library_in_and_out_record['刷卡時間']<'2013/01/11')]
library_in_and_out_record_101_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2013/01/11')&(library_in_and_out_record['刷卡時間']<'2013/06/26')]
library_in_and_out_record_102_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2013/06/26')&(library_in_and_out_record['刷卡時間']<'2014/01/14')]
library_in_and_out_record_102_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2014/01/14')&(library_in_and_out_record['刷卡時間']<'2014/06/20')]
library_in_and_out_record_103_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2014/06/20')&(library_in_and_out_record['刷卡時間']<'2015/01/27')]
library_in_and_out_record_103_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2015/01/27')&(library_in_and_out_record['刷卡時間']<'2015/06/30')]
library_in_and_out_record_104_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2015/06/30')&(library_in_and_out_record['刷卡時間']<'2016/01/15')]
library_in_and_out_record_104_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2016/01/15')&(library_in_and_out_record['刷卡時間']<'2016/06/21')]
library_in_and_out_record_105_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2016/06/21')&(library_in_and_out_record['刷卡時間']<'2017/01/13')]
library_in_and_out_record_105_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2017/01/13')&(library_in_and_out_record['刷卡時間']<'2017/06/23')]
library_in_and_out_record_106_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2017/06/23')&(library_in_and_out_record['刷卡時間']<'2018/01/19')]
library_in_and_out_record_106_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2018/01/19')&(library_in_and_out_record['刷卡時間']<'2018/06/29')]
library_in_and_out_record_107_up=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2018/06/29')&(library_in_and_out_record['刷卡時間']<'2019/01/11')]
#library_in_and_out_record_107_down=library_in_and_out_record[(library_in_and_out_record['刷卡時間']>='2019/01/11')&(library_in_and_out_record['刷卡時間']<'2019/06/21')]

In [15]:
#學生排名
#rank_train_100_up
rank_train_100_up=rank_train[(rank_train['學年']==100)&(rank_train['學期']==1)]
rank_train_100_down=rank_train[(rank_train['學年']==100)&(rank_train['學期']==2)]
rank_train_101_up=rank_train[(rank_train['學年']==101)&(rank_train['學期']==1)]
rank_train_101_down=rank_train[(rank_train['學年']==101)&(rank_train['學期']==2)]
rank_train_102_up=rank_train[(rank_train['學年']==102)&(rank_train['學期']==1)]
rank_train_102_down=rank_train[(rank_train['學年']==102)&(rank_train['學期']==2)]
rank_train_103_up=rank_train[(rank_train['學年']==103)&(rank_train['學期']==1)]
rank_train_103_down=rank_train[(rank_train['學年']==103)&(rank_train['學期']==2)]
rank_train_104_up=rank_train[(rank_train['學年']==104)&(rank_train['學期']==1)]
rank_train_104_down=rank_train[(rank_train['學年']==104)&(rank_train['學期']==2)]
rank_train_105_up=rank_train[(rank_train['學年']==105)&(rank_train['學期']==1)]
rank_train_105_down=rank_train[(rank_train['學年']==105)&(rank_train['學期']==2)]
rank_train_106_up=rank_train[(rank_train['學年']==106)&(rank_train['學期']==1)]
rank_train_106_down=rank_train[(rank_train['學年']==106)&(rank_train['學期']==2)]
rank_train_107_up=rank_train[(rank_train['學年']==107)&(rank_train['學期']==1)]
#rank_train_107_down=rank_train[(rank_train['學年']==107)&(rank_train['學期']==2)]

In [16]:
rank_train_107_up

學生   學年  年級  學期  概化排名  排名差
73595  003322731d5df9d33d40b43ec5c300f89d956c44  107   3   1    25   -4
73596  007a91bb90a8bfb3ac4ba999d252a35b824cbb8e  107   3   1    35    6
73597  0089869d4d8a20cc6b5ff2627152b9da60343469  107   3   1    15   13
73598  00c6deac1fdfde67fb46f73e1fc29ffb48526762  107   3   1    15    5
73599  00d718e3d99e68d643d3f76048a567a48249395b  107   3   1     5   13
...                                         ...  ...  ..  ..   ...  ...
75774  ff8a389ebdd2535ed7554a849c2a817ba389be95  107   3   1    75  -35
75775  ff9d99962346b12a3649459fdfeaee7e10c25491  107   3   1    55   -7
75776  ffa4caec29894fd871e78d68f3cd7f2766c5d6d4  107   3   1    45    1
75777  ffabe81c272b60ea2a34b987f066eb06c111439f  107   3   1     5   -2
75778  ffc26298937ceb5121fc50051c83c7aebb0f3588  107   3   1    15    2

[2184 rows x 6 columns]

In [17]:
# borrowing_record_100_up.to_csv("borrowing_record_100_up.csv")
# borrowing_record_101_up.to_csv("borrowing_record_101_up.csv")
# borrowing_record_102_up.to_csv("borrowing_record_102_up.csv")
# borrowing_record_103_up.to_csv("borrowing_record_103_up.csv")
# borrowing_record_104_up.to_csv("borrowing_record_104_up.csv")
# borrowing_record_105_up.to_csv("borrowing_record_105_up.csv")
# borrowing_record_106_up.to_csv("borrowing_record_106_up.csv")
# borrowing_record_107_up.to_csv("borrowing_record_107_up.csv")

# borrowing_record_100_down.to_csv("borrowing_record_100_down.csv")
# borrowing_record_101_down.to_csv("borrowing_record_101_down.csv")
# borrowing_record_102_down.to_csv("borrowing_record_102_down.csv")
# borrowing_record_103_down.to_csv("borrowing_record_103_down.csv")
# borrowing_record_104_down.to_csv("borrowing_record_104_down.csv")
# borrowing_record_105_down.to_csv("borrowing_record_105_down.csv")
# borrowing_record_106_down.to_csv("borrowing_record_106_down.csv")
# borrowing_record_107_down.to_csv("borrowing_record_107_down.csv")


In [18]:
print("學生借書筆數",len(borrowing_record_100_up))
print("學生修課筆數",len(course_train_100_up))
print("圖書館進出筆數",len(library_in_and_out_record_100_up))
print("學生排名筆數",len(rank_train_100_up))

學生借書筆數 24754
學生修課筆數 24514
圖書館進出筆數 32742
學生排名筆數 2000


# 查看沒有對照到排名的學生資料

In [19]:
no_borrowing=[]
borrowing_student=borrowing_record_100_up.drop_duplicates(subset=['學生'])
borrowing_student_index=borrowing_student.index
#borrowing_student.reset_index(drop=True,inplace=True)
for i in tqdm(borrowing_student_index):
    if(len(rank_train_100_up[rank_train_100_up['學生']==borrowing_student['學生'][i]])==0):
        no_borrowing.append(borrowing_student['學生'][i])

100%|████████████████████████████████████████████████████████████████████████████| 1941/1941 [00:01<00:00, 1365.46it/s]


In [20]:
no_course_train=[]
course_train_student=course_train_100_up.drop_duplicates(subset=['學生'])
course_train_student_index=course_train_student.index
#course_train_student.reset_index(drop=True,inplace=True)
for i in tqdm(course_train_student_index):
    if(len(rank_train_100_up[rank_train_100_up['學生']==course_train_student['學生'][i]])==0):
        no_course_train.append(course_train_student['學生'][i])

100%|████████████████████████████████████████████████████████████████████████████| 2000/2000 [00:01<00:00, 1385.05it/s]


In [21]:
no_library_in=[]
library_in_student=library_in_and_out_record_100_up.drop_duplicates(subset=['學生'])
library_in_student_index=library_in_student.index
#library_in_student.reset_index(drop=True,inplace=True)
for i in tqdm(library_in_student_index):
    if(len(rank_train_100_up[rank_train_100_up['學生']==library_in_student['學生'][i]])==0):
        no_library_in.append(library_in_student['學生'][i])

100%|████████████████████████████████████████████████████████████████████████████| 3154/3154 [00:02<00:00, 1370.83it/s]


In [22]:
print("借書學生沒有排名",len(no_borrowing))
print("修課學生沒有排名",len(no_course_train))
print("進出學生沒有排名",len(no_library_in))

借書學生沒有排名 933
修課學生沒有排名 0
進出學生沒有排名 1680


In [23]:
#######################
#如果有沒有的資料進行移除
#######################

In [24]:
print("刪除前借書學生",len(borrowing_record_100_up))
print("刪除前修課學生",len(course_train_100_up))
print("刪除前借書學生",len(library_in_and_out_record_100_up))

刪除前借書學生 24754
刪除前修課學生 24514
刪除前借書學生 32742


In [25]:
for i in tqdm(range(len(no_borrowing))):
    no_borrowing_index=borrowing_record_100_up[borrowing_record_100_up['學生']==no_borrowing[i]].index
    borrowing_record_100_up.drop(index=no_borrowing_index,inplace=True)

  0%|                                                                                          | 0/933 [00:00<?, ?it/s]c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\pandas\core\frame.py:4174: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
100%|███████████████████████████████████████████████████████████████████████████████| 933/933 [00:06<00:00, 142.61it/s]


In [26]:
for i in tqdm(range(len(no_course_train))):
    no_course_train_index=course_train_100_up[course_train_100_up['學生']==no_course_train[i]].index
    course_train_100_up.drop(index=no_course_train_index,inplace=True)

0it [00:00, ?it/s]


In [27]:
for i in tqdm(range(len(no_library_in))):
    no_library_in_index=library_in_and_out_record_100_up[library_in_and_out_record_100_up['學生']==no_library_in[i]].index
    library_in_and_out_record_100_up.drop(index=no_library_in_index,inplace=True)

100%|█████████████████████████████████████████████████████████████████████████████| 1680/1680 [00:08<00:00, 192.25it/s]


In [28]:
borrowing_record_100_up.reset_index(drop=True,inplace=True)
course_train_100_up.reset_index(drop=True,inplace=True)
library_in_and_out_record_100_up.reset_index(drop=True,inplace=True)

In [29]:
print("刪除後借書學生",len(borrowing_record_100_up))
print("刪除後修課學生",len(course_train_100_up))
print("刪除後借書學生",len(library_in_and_out_record_100_up))

刪除後借書學生 16118
刪除後修課學生 24514
刪除後借書學生 17322


# 館藏索書號對照類別

In [31]:
#將書籍資料前面多餘的值刪除
characters = "DVD"

for i in range(len(borrowing_record_100_up)):
    if characters in borrowing_record_100_up['館藏索書號'][i]:
        for x in range(len(characters)):
            borrowing_record_100_up['館藏索書號'][i]=borrowing_record_100_up['館藏索書號'][i].replace(characters[x],"")

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)


In [32]:
borrowing_record_100_up['館藏索書號'].replace('\s+','',regex=True,inplace=True)

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\pandas\core\series.py:4581: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  method=method,


In [33]:
eng_begin=[]
for i in range(len(borrowing_record_100_up)):
    if re.match('([a-z|A-Z])',borrowing_record_100_up['館藏索書號'][i]):
        eng_begin.append(i)

In [34]:
borrowing_record_100_up_english=borrowing_record_100_up.iloc[eng_begin]
borrowing_record_100_up_chinese=borrowing_record_100_up.drop(index=eng_begin)

borrowing_record_100_up_english.reset_index(drop=True,inplace=True)
borrowing_record_100_up_chinese.reset_index(drop=True,inplace=True)

In [35]:
#中文圖書分類法(數字)

In [36]:
#沒對照中文:0
#沒對照英文:1
#對照中文:2
#對照西方:3
#對照醫學:4

In [37]:
chinese_index=[]
no_chinese_index=[]
chinese_num=[]
no_chinese_array=np.array(["無中文類"], dtype='object')
index=borrowing_record_100_up_chinese['館藏索書號'].apply(lambda x:x[:3])
for i in tqdm(range(len(index))):
    chinese_class=int(index[i])
    if(len(chinese[chinese['分類號']==chinese_class])>0):
        chinese_index.append(chinese[chinese['分類號']==chinese_class]['分類項目名稱'])
        chinese_num.append(2)
    else:
        chinese_index.append(no_chinese_array)
        no_chinese_index.append(i)
        chinese_num.append(0)

100%|███████████████████████████████████████████████████████████████████████████| 15919/15919 [00:24<00:00, 660.69it/s]


In [38]:
print("原先資料筆數:",len(index))
print("對照數字筆數:",len(chinese_num))
print("對照資料筆數:",len(chinese_index)-len(no_chinese_index))
print("沒有對照類別:",len(no_chinese_index))

原先資料筆數: 15919
對照數字筆數: 15919
對照資料筆數: 15831
沒有對照類別: 88


In [39]:
chinese_index=pd.DataFrame(np.concatenate(chinese_index,axis=0),columns=['class'])
chinese_num=pd.DataFrame(chinese_num,columns=['class_num'])
chinese_merge=pd.concat([chinese_index,chinese_num],axis=1)
chinese_merge.head()

class  class_num
0   臨床心理          2
1  社會學各論          2
2  社會學各論          2
3  社會學各論          2
4   臨床心理          2

In [40]:
#英文圖書分類法(英文)

In [41]:
index2=[]
for i in range(len(borrowing_record_100_up_english)):
    index2.append(re.split(r'(\d+)', borrowing_record_100_up_english['館藏索書號'][i])[0])

In [42]:
western_index=[]
america_index=[]
english_num=[]
no_english_index=[]
no_english_array=np.array(["無英文類"], dtype='object')
for i in tqdm(range(len(index2))):
    if(len(western[western['Unnamed: 2']==index2[i]])>0):
        western_index.append(western[western['Unnamed: 2']==index2[i]]['美國國會分類法(LCC)'].values)
        english_num.append(3)
    elif(len(america[america['分類號']==index2[i]])>0):
        western_index.append(america[america['分類號']==index2[i]]['內容'])
        america_index.append(america[america['分類號']==index2[i]]['內容'])  
        english_num.append(4)
    else:
        western_index.append(no_english_array)
        no_english_index.append(i)
        english_num.append(1)

100%|███████████████████████████████████████████████████████████████████████████████| 199/199 [00:00<00:00, 702.53it/s]


In [43]:
print("原先資料筆數:",len(index2))
print("對照數字筆數:",len(english_num))
print("對照英文資料:",len(western_index)-len(america_index)-len(no_english_index))
print("對照醫學資料:",len(america_index))
print("沒有對照類別:",len(no_english_index))

原先資料筆數: 199
對照數字筆數: 199
對照英文資料: 191
對照醫學資料: 0
沒有對照類別: 8


In [44]:
western_index=pd.DataFrame(np.concatenate(western_index,axis=0),columns=['class'])
english_num=pd.DataFrame(english_num,columns=['class_num'])
english_merge=pd.concat([western_index,english_num],axis=1)
english_merge.head()

class  class_num
0  B ─ PHILOSOPHY. PSYCHOLOGY. RELIGION          3
1  B ─ PHILOSOPHY. PSYCHOLOGY. RELIGION          3
2           P ─ LANGUAGE AND LITERATURE          3
3                   H ─ SOCIAL SCIENCES          3
4           P ─ LANGUAGE AND LITERATURE          3

# 再次確認學生排名資料有無重複

In [45]:
rank_train_100_up.sort_values('學生',inplace=True)
rank_train_100_up['學生'].value_counts()

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


ea2e4ec3786bc30dec229a17fc36efb769314220    1
e4b36cca8d7100f7f5620443fb96fe1441189d2d    1
ebc063d2935daec360613a890f017dd976ee25b5    1
6162d15d6d4c6179625508f65ac75bab09442d84    1
4edf6740b4e7ad10275d4c43b26dd47f0ec39e24    1
                                           ..
94a95fba3a7a4196b34164d613bf9cfc942de76c    1
02468602809cab3fd25aead6839d48b85adb008c    1
a59b4c4ab03a2ce03e08a95883d8ea28ae599180    1
90fcf7d923d26c3fe594ccda53e8b418a1ce97f2    1
09dbc820a4dd59a68c013d024b73e4401dff4e86    1
Name: 學生, Length: 2000, dtype: int64

In [46]:
rank_train_100_up[['系所','必修課程數','選修課程數','學分']]=0
rank_train_100_up[['借中文書次數','借西方書次數','借醫學書次數','借中文書無對照','借英文書無對照']]=0
rank_train_100_up['進出圖書館次數']=0
rank_train_100_up.head()

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\pandas\core\indexing.py:659: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[k] = np.nan
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\pandas\core\indexing.py:1763: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
T

學生   學年  年級  學期  概化排名  排名差  系所  \
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  100   1   1     5    0   0   
1  0008612986afce01d430baec13e6ab111ff864a9  100   1   1   105    0   0   
2  002aad264dbe66aeaf7ddfbd5afffd22e3930588  100   1   1    45    0   0   
3  0037f157b190f25f6e06030ea2c5f9f62b429ea1  100   1   1    55    0   0   
4  003a5db190ba04e18cbedba93306e7ebee670d96  100   1   1     5    0   0   

   必修課程數  選修課程數  學分  借中文書次數  借西方書次數  借醫學書次數  借中文書無對照  借英文書無對照  進出圖書館次數  
0      0      0   0       0       0       0        0        0        0  
1      0      0   0       0       0       0        0        0        0  
2      0      0   0       0       0       0        0        0        0  
3      0      0   0       0       0       0        0        0        0  
4      0      0   0       0       0       0        0        0        0

In [47]:
rank_train_100_up.reset_index(drop=True,inplace=True)

# 合併書籍類別資料

In [48]:
chinese_fin=pd.concat([borrowing_record_100_up_chinese,chinese_merge],axis=1)
english_fin=pd.concat([borrowing_record_100_up_english,english_merge],axis=1)

In [49]:
for i in range(len(rank_train_100_up)):
    chinese_student=chinese_fin[chinese_fin['學生']==rank_train_100_up['學生'][i]]
    if(len(chinese_student)>0):
        no_chinese=len(chinese_student[chinese_student['class_num']==0])
        chinese=len(chinese_student[chinese_student['class_num']==2])
        if(no_chinese>0):
            rank_train_100_up['借中文書無對照'][i]=no_chinese
        if(chinese>0):
            rank_train_100_up['借中文書次數'][i]=chinese

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_

...

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

In [50]:
for i in range(len(rank_train_100_up)):
    english_student=english_fin[english_fin['學生']==rank_train_100_up['學生'][i]]
    if(len(english_student)>0):
        no_english=len(english_student[english_student['class_num']==1])
        western=len(english_student[english_student['class_num']==3])
        america=len(english_student[english_student['class_num']==4])
        if(no_english>0):
            rank_train_100_up['借英文書無對照'][i]=no_english
        if(western>0):
            rank_train_100_up['借西方書次數'][i]=western
        if(america>0):
            rank_train_100_up['借醫學書次數'][i]=america

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-ve

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.or

In [51]:
rank_train_100_up.head()

學生   學年  年級  學期  概化排名  排名差  系所  \
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  100   1   1     5    0   0   
1  0008612986afce01d430baec13e6ab111ff864a9  100   1   1   105    0   0   
2  002aad264dbe66aeaf7ddfbd5afffd22e3930588  100   1   1    45    0   0   
3  0037f157b190f25f6e06030ea2c5f9f62b429ea1  100   1   1    55    0   0   
4  003a5db190ba04e18cbedba93306e7ebee670d96  100   1   1     5    0   0   

   必修課程數  選修課程數  學分  借中文書次數  借西方書次數  借醫學書次數  借中文書無對照  借英文書無對照  進出圖書館次數  
0      0      0   0       6       0       0        0        0        0  
1      0      0   0       0       0       0        0        0        0  
2      0      0   0       0       0       0        0        0        0  
3      0      0   0       2       0       0        0        0        0  
4      0      0   0      22       0       0        0        0        0

# 合併學生選課資料

In [52]:
for i in range(len(rank_train_100_up)):
    student=course_train_100_up[course_train_100_up['學生']==rank_train_100_up['學生'][i]]
    student.drop_duplicates(subset=['課程代碼'],inplace=True)
    if(len(student)>0):    
        must=len(student[(student['修別']=='必修') & (student['學分']>0)])
        choose=len(student[(student['修別']=='選修') & (student['學分']>0)])
        credit=sum(student['學分'])
        rank_train_100_up['系所'][i]=student.iloc[0]['系所']
        if(must>0):
            rank_train_100_up['必修課程數'][i]=must
        if(choose>0):
            rank_train_100_up['選修課程數'][i]=choose
        if(credit>0):
            rank_train_100_up['學分'][i]=credit

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-ve

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

...

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-ve

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-ve

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

In [53]:
rank_train_100_up.head()

學生   學年  年級  學期  概化排名  排名差  \
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  100   1   1     5    0   
1  0008612986afce01d430baec13e6ab111ff864a9  100   1   1   105    0   
2  002aad264dbe66aeaf7ddfbd5afffd22e3930588  100   1   1    45    0   
3  0037f157b190f25f6e06030ea2c5f9f62b429ea1  100   1   1    55    0   
4  003a5db190ba04e18cbedba93306e7ebee670d96  100   1   1     5    0   

                  系所  必修課程數  選修課程數  學分  借中文書次數  借西方書次數  借醫學書次數  借中文書無對照  \
0             資訊傳播學系      2      2   8       6       0       0        0   
1             資訊傳播學系      9      0  22       0       0       0        0   
2  資訊多媒體應用學系(多媒體應用組)      7      0  18       0       0       0        0   
3               心理學系      8      0  20       2       0       0        0   
4      財務金融學系(投資管理組)      8      0  19      22       0       0        0   

   借英文書無對照  進出圖書館次數  
0        0        0  
1        0        0  
2        0        0  
3        0        0  
4        0        0

# 合併進出圖書館次數

In [54]:
library_in_num=pd.DataFrame(library_in_and_out_record_100_up['學生'].value_counts())
library_in_num.reset_index(drop=False,inplace=True)
library_in_num.columns = ['學生','進出次數']
library_in_num.sort_values('學生',inplace=True)
library_in_num.reset_index(drop=True,inplace=True)

In [55]:
for i in range(len(rank_train_100_up)):
    student=library_in_num[library_in_num['學生']==rank_train_100_up['學生'][i]]
    if(len(student)>0): 
        rank_train_100_up['進出圖書館次數'][i]=student.iloc[0]['進出次數']

c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
c:\users\user\anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:3343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)


In [56]:
rank_train_100_up.head()

學生   學年  年級  學期  概化排名  排名差  \
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  100   1   1     5    0   
1  0008612986afce01d430baec13e6ab111ff864a9  100   1   1   105    0   
2  002aad264dbe66aeaf7ddfbd5afffd22e3930588  100   1   1    45    0   
3  0037f157b190f25f6e06030ea2c5f9f62b429ea1  100   1   1    55    0   
4  003a5db190ba04e18cbedba93306e7ebee670d96  100   1   1     5    0   

                  系所  必修課程數  選修課程數  學分  借中文書次數  借西方書次數  借醫學書次數  借中文書無對照  \
0             資訊傳播學系      2      2   8       6       0       0        0   
1             資訊傳播學系      9      0  22       0       0       0        0   
2  資訊多媒體應用學系(多媒體應用組)      7      0  18       0       0       0        0   
3               心理學系      8      0  20       2       0       0        0   
4      財務金融學系(投資管理組)      8      0  19      22       0       0        0   

   借英文書無對照  進出圖書館次數  
0        0        3  
1        0        1  
2        0        1  
3        0        1  
4        0       57

In [ ]:
rank_train_100_up.to_csv("Train_100_1.csv")

# 合併每學年資料

In [3]:
df1 = pd.read_csv("Train_100_1.csv",index_col=0)
df2 = pd.read_csv("Train_100_2.csv",index_col=0)
df3 = pd.read_csv("Train_101_1.csv",index_col=0)
df4 = pd.read_csv("Train_101_2.csv",index_col=0)
df5 = pd.read_csv("Train_102_1.csv",index_col=0)
df6 = pd.read_csv("Train_102_2.csv",index_col=0)
df7 = pd.read_csv("Train_103_1.csv",index_col=0)
df8 = pd.read_csv("Train_103_2.csv",index_col=0)
df9 = pd.read_csv("Train_104_1.csv",index_col=0)
df10 = pd.read_csv("Train_104_2.csv",index_col=0)
df11 = pd.read_csv("Train_105_1.csv",index_col=0)
df12 = pd.read_csv("Train_105_2.csv",index_col=0)
df13 = pd.read_csv("Train_106_1.csv",index_col=0)
df14 = pd.read_csv("Train_106_2.csv",index_col=0)
df15 = pd.read_csv("Train_107_1.csv",index_col=0)

In [4]:
df = pd.concat([df1,df2,df3,df4,df5,df6,df7,df8,df9,df10,df11,df12,df13,df14,df15])
df.reset_index(drop=True,inplace=True)
print(df.shape)
df.head()

(75779, 16)


學生   學年  年級  學期  概化排名  排名差  \
0  0003764c18b55548b8e7e0a064fed87fb46fa2a2  100   1   1     5    0   
1  0008612986afce01d430baec13e6ab111ff864a9  100   1   1   105    0   
2  002aad264dbe66aeaf7ddfbd5afffd22e3930588  100   1   1    45    0   
3  0037f157b190f25f6e06030ea2c5f9f62b429ea1  100   1   1    55    0   
4  003a5db190ba04e18cbedba93306e7ebee670d96  100   1   1     5    0   

                  系所  必修課程數  選修課程數  學分  借中文書次數  借西方書次數  借醫學書次數  借中文書無對照  \
0             資訊傳播學系      2      2   8       6       0       0        0   
1             資訊傳播學系      9      0  22       0       0       0        0   
2  資訊多媒體應用學系(多媒體應用組)      7      0  18       0       0       0        0   
3               心理學系      8      0  20       2       0       0        0   
4      財務金融學系(投資管理組)      8      0  19      22       0       0        0   

   借英文書無對照  進出圖書館次數  
0        0        3  
1        0        1  
2        0        1  
3        0        1  
4        0       57

In [5]:
df.sort_values(['學年','學期','年級','學生'],inplace=True)

In [6]:
df_test_fin=df[(df['學年']==107) & (df['學期']==1)]
df_drop_index=df_test_fin.index
df_test_fin.head()

學生   學年  年級  學期  概化排名  排名差  \
73595  003322731d5df9d33d40b43ec5c300f89d956c44  107   3   1    25   -4   
73596  007a91bb90a8bfb3ac4ba999d252a35b824cbb8e  107   3   1    35    6   
73597  0089869d4d8a20cc6b5ff2627152b9da60343469  107   3   1    15   13   
73598  00c6deac1fdfde67fb46f73e1fc29ffb48526762  107   3   1    15    5   
73599  00d718e3d99e68d643d3f76048a567a48249395b  107   3   1     5   13   

                      系所  必修課程數  選修課程數  學分  借中文書次數  借西方書次數  借醫學書次數  借中文書無對照  \
73595  健康產業管理學系(醫療機構管理組)      4      7  25       1       0       0        0   
73596             時尚設計學系      3      6  21       7       2       0        0   
73597  健康產業管理學系(醫療機構管理組)      2      7  19       0       0       0        0   
73598           創意商品設計學系      3      4  20       0       0       0        0   
73599             社會工作學系      2      6  18       9       0       0        0   

       借英文書無對照  進出圖書館次數  
73595        0        9  
73596        0       20  
73597        0        1  
73598        0        2  
73599        0       20

In [ ]:
col=['學生','學年','年級','學期','概化排名','排名差','系所','必修課程數','選修課程數','學分','借中文書次數','借西方書次數','借醫學書次數','借中文書無對照','借英文書無對照','進出圖書館次數']
qqq=pd.DataFrame(df,columns=col)
qqq.to_csv("Library_fin.csv")